<img src="http://developer.download.nvidia.com/notebooks/dlsw-notebooks/riva_tts_tts-python-basics/nvidia_logo.png" style="width: 90px; float: right;">

# Riva NMT NIM Tutorial

This tutorial walks you through the various features of Riva NMT NIM and how to the APIs in a Python application. Riva NMT NIM uses [gRPC API](https://grpc.io/).

## Prerequisites

1. Deploy the Riva Translate 1.6b model using [Riva NMT NIM documentation](https://docs.nvidia.com/nim/riva/nmt/latest/overview.html).
2. Install the Riva Python Client library:

    ```bash
    sudo apt-get install python3-pip
    pip install -U nvidia-riva-client
    ```

#### Import Riva Client Libraries

Begin by importing some of the necessary libraries, including the Riva Client libraries.

In [ ]:
# Import required libraries
import io
import wave
from pathlib import Path
import riva.client

print("Using Riva Python Client version: ", riva.client.__version__)

#### Create Riva clients and connect to the Riva server

The following URI assumes a local deployment of the Riva TTS NIM on the default port. In case the server deployment is on a different host or via Helm chart on Kubernetes, use an appropriate URI.

In [4]:
auth = riva.client.Auth(uri='0.0.0.0:50051')
nmt_client = riva.client.NeuralMachineTranslationClient(auth)

#### Get list of supported languages.

In [ ]:
response = nmt_client.get_config(model="")
print(response)

#### Perform Single Translation

In [ ]:
inputs = ["Riva Translate is a neural machine translation model that translates text between languages."]
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="fr")
print(response)

#### Perform Batch Translation

Riva Translate supports batched inference of multiple inputs to provide a faster translation experience. Using the translation client, one can batch together up to 8 inputs and translate them in a single request.

In [ ]:
inputs = ["I think, therefore I am.", "To be, or not to be: that is the question.", "The only thing we have to fear is fear itself.",
          "So many books, so little time.", "If you tell the truth, you don't have to remember anything.", "Without music, life would be a mistake.",
          "The world is a book, and those who do not travel read only one page.", "The only way to do great work is to love what you do."]
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="hi")
print(response)

#### Translation Exclusion

Text enclosed with `<dnt>` and `</dnt>` tags is not translated.

In [ ]:
inputs = ["<dnt>Riva translate</dnt> model translates audio between language pairs."]
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="fr")
print(response)

#### Custom Translation Dictionary

A dictionary can be used to provide custom translations or to avoid translating certain words.

In [ ]:
inputs = ["bad morning everyone."]
dnt_phrases_dict = {"bad": "good", "everyone": ""}
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="fr-FR", dnt_phrases_dict=dnt_phrases_dict)
print(response)

#### Morphologically Complex Translations

In [ ]:
inputs = ["Agentic AI uses sophisticated reasoning and iterative planning to autonomously solve complex, multi-step problems."]
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="ar")
print(response)


Translations using the default value of `max_len_variation` (default: `20`) lead to incomplete translations for morphologically rich languages. In such cases, setting a higher value allows the model to accommodate a larger variation between the number of source tokens and translated tokens. Increasing the value of `max_len_variations` will lead to higher inference latency. This increase in latency is typically observed only if the target language actually requires more tokens to translate faithfully.

In [ ]:
inputs = ["Agentic AI uses sophisticated reasoning and iterative planning to autonomously solve complex, multi-step problems."]
response = nmt_client.translate(inputs, model="", source_language="en-US", target_language="ar", max_len_variation="100")
print(response)